# Решение задачи Коммивояжера

In [2]:
from math import sqrt
from time import time
from typing import List, Tuple

import folium
import numpy as np
import pandas as pd
from tqdm import tqdm

In [3]:
data = pd.read_csv('../data/data.csv', delimiter=',')
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6137 entries, 0 to 6136
Data columns (total 7 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   id            6137 non-null   int64 
 1   region        6137 non-null   object
 2   municipality  6137 non-null   object
 3   settlement    6137 non-null   object
 4   type          6137 non-null   object
 5   latitude_dd   6137 non-null   int64 
 6   longitude_dd  6137 non-null   int64 
dtypes: int64(3), object(4)
memory usage: 335.7+ KB


In [4]:
data['type'].value_counts()

с    3045
д    1654
п    1327
г     111
Name: type, dtype: int64

Покажем расположение населённых пунктов на карте

In [4]:
map_ = folium.Map(
    location=[64.0914, 101.6016],
    tiles='Stamen Toner',
    zoom_start=3
)

In [5]:
for index, row in data.iterrows():
    folium.Circle(
        radius=100,
        location=[row['latitude_dd']/100, row['longitude_dd']/100],
        popup=row['settlement'],
        color='crimson',
        fill=True,
    ).add_to(map_)

map_

In [6]:
def calculate_distance_matrix(cities_dataframe):
    n = len(cities_dataframe)
    city_dist_matrix = np.zeros((n, n))
    total_iterations = n * (n - 1) // 2
    iterations_done = 0
    for i in range(n):
        for j in range(i + 1, n):
            coords_i = (cities_dataframe.loc[i, 'latitude_dd'], cities_dataframe.loc[i, 'longitude_dd'])
            coords_j = (cities_dataframe.loc[j, 'latitude_dd'], cities_dataframe.loc[j, 'longitude_dd'])
            dist = euclidean_distance(*coords_i, *coords_j)
            city_dist_matrix[i, j] = dist
            city_dist_matrix[j, i] = dist
            iterations_done += 1
            if iterations_done % 1000 == 0:
                print(f'Calculating distance matrix: {iterations_done}/{total_iterations} iterations done')
    return city_dist_matrix


def euclidean_distance(x1, y1, x2, y2):
    return sqrt((x1 - x2) ** 2 + (y1 - y2) ** 2)


def find_len(matrix, way):
    return sum([matrix[way[_]][way[_ + 1]] for _ in range(0, len(way) - 1)]) / 100


def route_distance(route, cities_dist_matrix):
    n = len(route)
    total_distance = 0
    for _ in range(n):
        city1 = route[_]
        city2 = route[(_ + 1) % n]
        total_distance += cities_dist_matrix[city1][city2]
    return total_distance


def display_final_route(distance_matrix: np.ndarray, city_data: pd.DataFrame, optimal_route: np.ndarray) -> folium.Map:
    # Вычисление общего расстояния финального маршрута
    optimal_score = route_distance(optimal_route, distance_matrix)

    # Создание списка пар широты/долготы для каждого города в финальном маршруте
    route_latlon: List[Tuple[float, float]] = []
    for city_id in optimal_route:
        city = city_data.loc[city_data["id"] == city_id]
        route_latlon.append((city["latitude_dd"].values[0] / 100, city["longitude_dd"].values[0] / 100))

    # Создание объекта folium.Map для отображения финального маршрута на карте
    map_route = folium.Map(location=[64.0914, 101.6016], tiles='Stamen Toner', zoom_start=3)
    for i, city in enumerate(route_latlon):
        folium.Circle(city, popup=city_data.loc[city_data["id"] == optimal_route[i]]["settlement"].values[0]).add_to(
            map_route)
        if i < len(route_latlon) - 1:
            folium.PolyLine([route_latlon[i], route_latlon[i + 1]], color="red").add_to(map_route)

    # Отображение карты
    return map_route

In [15]:
dist_matrix = calculate_distance_matrix(data)

# Сохранение данных в CSV-файл
np.savetxt('dist_matrix.csv', dist_matrix, delimiter=',', fmt='%.4f')

Calculating distance matrix: 1000/18828316 iterations done
Calculating distance matrix: 2000/18828316 iterations done
Calculating distance matrix: 3000/18828316 iterations done
Calculating distance matrix: 4000/18828316 iterations done
Calculating distance matrix: 5000/18828316 iterations done
Calculating distance matrix: 6000/18828316 iterations done
Calculating distance matrix: 7000/18828316 iterations done
Calculating distance matrix: 8000/18828316 iterations done
Calculating distance matrix: 9000/18828316 iterations done
Calculating distance matrix: 10000/18828316 iterations done
Calculating distance matrix: 11000/18828316 iterations done
Calculating distance matrix: 12000/18828316 iterations done
Calculating distance matrix: 13000/18828316 iterations done
Calculating distance matrix: 14000/18828316 iterations done
Calculating distance matrix: 15000/18828316 iterations done
Calculating distance matrix: 16000/18828316 iterations done
Calculating distance matrix: 17000/18828316 itera

## Загрузка матрицы из CSV-файла

In [3]:
dist_matrix = np.loadtxt('dist_matrix.csv', delimiter=',')

## Жадный алгоритм

In [4]:
def find_shortest_path(matrix: np.ndarray, start_vertex: int = 0, output_file: str = "way.csv") -> np.ndarray:
    """
    Find the shortest path in a graph using a greedy algorithm.

    :param matrix: Adjacency matrix representing the graph.
    :param start_vertex: Starting vertex for the algorithm.
    :param output_file: File path to save the shortest path found.
    :return: Array of vertices representing the shortest path found.
    """
    num_vertices = matrix.shape[0]
    visited = np.zeros(num_vertices, dtype=bool)
    current_vertex = start_vertex
    path = np.zeros(num_vertices + 1, dtype=int)

    for _ in range(num_vertices):
        visited[current_vertex] = True
        min_distance = np.inf
        next_vertex = -1
        for j in range(num_vertices):
            if j != current_vertex and not visited[j]:
                distance = matrix[current_vertex, j]
                if distance < min_distance:
                    min_distance = distance
                    next_vertex = j
        path[_] = current_vertex
        current_vertex = next_vertex

    path[num_vertices] = path[0]
    np.savetxt(output_file, path, fmt="%d")

    return path

In [7]:
greedy_route = find_shortest_path(dist_matrix, 3753, output_file="way.csv")
greedy_score = route_distance(greedy_route, dist_matrix)
print(f'Total distance: {greedy_score}')
print(f'Жадный алгоритм: {find_len(dist_matrix, greedy_route)}')

Total distance: 107437.89600000018
Жадный алгоритм: 1074.3789600000018


## Алгоритм 2-opt

In [8]:
def two_opt(route, cities_dist_matrix):
    """

    :param route:
    :param cities_dist_matrix:
    :return:
    """
    n = len(route)
    improved = True
    pbar = tqdm(total=n)
    while improved:
        improved = False
        for _ in range(1, n - 2):
            pbar.update(1)
            for j in range(_ + 1, n - 1):
                city1 = route[_ - 1]
                city2 = route[_]
                city3 = route[j]
                city4 = route[(j + 1) % n]
                old_distance = cities_dist_matrix[city1][city2] + cities_dist_matrix[city3][city4]
                new_distance = cities_dist_matrix[city1][city3] + cities_dist_matrix[city2][city4]
                if new_distance < old_distance:
                    route[_:j + 1] = list(reversed(route[_:j + 1]))
                    improved = True
    pbar.close()
    return route

In [9]:
two_opt_route = two_opt(greedy_route, dist_matrix)
two_opt_score = route_distance(greedy_route, dist_matrix)
print(f'Total distance: {two_opt_score}')
print(f'2-opt алгоритм, улучшение: {find_len(dist_matrix, two_opt_route)}')

42945it [04:25, 161.99it/s]                          

Total distance: 91300.34190000009
2-opt алгоритм, улучшение: 913.0034190000009


## Улучшенный алгоритм 2-opt

In [ ]:
def two_opt_with_tabu_search(route, cities_dist_matrix, max_iterations=1000, tabu_tenure=10):
    """

    :param route:
    :param cities_dist_matrix:
    :param max_iterations:
    :param tabu_tenure:
    :return:
    """
    n = len(route)
    best_route = route
    best_score = route_distance(route, cities_dist_matrix)
    tabu_list = []
    pbar = tqdm(total=max_iterations)
    for iteration in range(max_iterations):
        pbar.update(1)
        # Find the best 2-opt move that is not tabu
        best_move = None
        best_move_score = float('inf')
        for i in range(1, n - 2):
            for j in range(i + 1, n - 1):
                if (i, j) not in tabu_list:
                    city1 = route[i - 1]
                    city2 = route[i]
                    city3 = route[j]
                    city4 = route[(j + 1) % n]
                    old_distance = cities_dist_matrix[city1][city2] + cities_dist_matrix[city3][city4]
                    new_distance = cities_dist_matrix[city1][city3] + cities_dist_matrix[city2][city4]
                    move_score = new_distance - old_distance
                    if move_score < best_move_score:
                        best_move = (i, j)
                        best_move_score = move_score
        # Make the best move and update the tabu list
        if best_move is not None:
            i, j = best_move
            route[i:j + 1] = list(reversed(route[i:j + 1]))
            tabu_list.append(best_move)
            if len(tabu_list) > tabu_tenure:
                tabu_list.pop(0)
        # Update the best solution
        current_score = route_distance(route, cities_dist_matrix)
        if current_score < best_score:
            best_route = route
            best_score = current_score
        print(f'Iteration {iteration}: Best score = {best_score / 100}')
    pbar.close()
    return best_route

In [ ]:
better_opt_route = two_opt_with_tabu_search(greedy_route, dist_matrix)
better_opt_score = route_distance(greedy_route, dist_matrix)
print(f'Total distance: {better_opt_score}')
print(f'Улучшенный 2-opt алгоритм: {find_len(dist_matrix, better_opt_route)}')

In [ ]:
from csv import DictWriter

with open("../data/submission.csv", "w", encoding="utf-8") as csv:
    writer = DictWriter(
        csv, delimiter=",", lineterminator="\r",
        fieldnames=["PassengerId", "Survived"]
    )
    writer.writeheader()